In [1]:
from pedalboard import Pedalboard, Reverb, load_plugin
from pedalboard.io import AudioFile
from mido import Message

In [2]:
# Open Vital plugin
vital = load_plugin("/home/benjamin/Documents/work/Synthetizers-parameters-estimation/plugins/Vital.vst3")
print(vital.parameters.keys())

dict_keys(['beats_per_minute', 'chorus_filter_cutoff', 'chorus_delay_1', 'chorus_delay_2', 'chorus_mix', 'chorus_feedback', 'chorus_frequency', 'chorus_mod_depth', 'chorus_switch', 'chorus_sync', 'chorus_tempo', 'compressor_attack', 'compressor_band_gain', 'band_lower_ratio', 'band_lower_threshold', 'band_upper_ratio', 'band_upper_threshold', 'compressor_enabled_bands', 'compressor_high_gain', 'high_lower_ratio', 'high_lower_threshold', 'high_upper_ratio', 'high_upper_threshold', 'compressor_low_gain', 'low_lower_ratio', 'low_lower_threshold', 'low_upper_ratio', 'low_upper_threshold', 'compressor_switch', 'compressor_release', 'delay_mix', 'delay_feedback', 'delay_filter_cutoff', 'delay_filter_spread', 'delay_frequency', 'delay_switch', 'delay_style', 'delay_sync', 'delay_tempo', 'distortion_drive', 'distortion_filter_blend', 'distortion_filter_cutoff', 'distortion_filter_order', 'distortion_filter_resonance', 'distortion_mix', 'distortion_switch', 'distortion_type', 'effect_chain_orde

In [3]:
# Play a note: C4 (MIDI note 60) with velocity 0.8
sample_rate = 44100
audio = vital(
  [Message("note_on", note=60), Message("note_off", note=60, time=5)],
  duration=5, # seconds
  sample_rate=sample_rate,
)

from IPython.display import Audio
Audio(audio, rate=sample_rate)

In [4]:
import json

file = 'preset.vital'
with open(file, '+r') as f:
    preset_data = json.load(f)

In [5]:
print(preset_data.keys())

dict_keys(['author', 'comments', 'macro1', 'macro2', 'macro3', 'macro4', 'preset_name', 'preset_style', 'settings', 'synth_version'])


In [6]:
print(preset_data['settings'].keys())

dict_keys(['beats_per_minute', 'bypass', 'chorus_cutoff', 'chorus_delay_1', 'chorus_delay_2', 'chorus_dry_wet', 'chorus_feedback', 'chorus_frequency', 'chorus_mod_depth', 'chorus_on', 'chorus_spread', 'chorus_sync', 'chorus_tempo', 'chorus_voices', 'compressor_attack', 'compressor_band_gain', 'compressor_band_lower_ratio', 'compressor_band_lower_threshold', 'compressor_band_upper_ratio', 'compressor_band_upper_threshold', 'compressor_enabled_bands', 'compressor_high_gain', 'compressor_high_lower_ratio', 'compressor_high_lower_threshold', 'compressor_high_upper_ratio', 'compressor_high_upper_threshold', 'compressor_low_gain', 'compressor_low_lower_ratio', 'compressor_low_lower_threshold', 'compressor_low_upper_ratio', 'compressor_low_upper_threshold', 'compressor_mix', 'compressor_on', 'compressor_release', 'delay_aux_frequency', 'delay_aux_sync', 'delay_aux_tempo', 'delay_dry_wet', 'delay_feedback', 'delay_filter_cutoff', 'delay_filter_spread', 'delay_frequency', 'delay_on', 'delay_sty

In [7]:
print(len(set(preset_data["settings"].keys())))
print(len(vital.parameters.keys()))

776
775


In [8]:
# Number of keys in intersection
common_keys = set(preset_data["settings"].keys()).intersection(set(vital.parameters.keys()))
print(len(common_keys))

519


In [9]:
# Show keys in preset but not in vital parameters
preset_only_keys = set(preset_data["settings"].keys()) - set(vital.parameters.keys())
print(preset_only_keys)

# Show keys in vital parameters but not in preset
vital_only_keys = set(vital.parameters.keys()) - set(preset_data["settings"].keys())
print(vital_only_keys)

{'osc_2_unison_voices', 'env_3_decay_power', 'env_1_attack_power', 'flanger_dry_wet', 'reverb_dry_wet', 'env_2_decay', 'osc_2_spectral_unison', 'filter_1_blend_transpose', 'osc_3_unison_voices', 'env_6_decay', 'osc_3_smooth_interpolation', 'random_4_keytrack_tune', 'chorus_spread', 'osc_2_distortion_phase', 'osc_1_tune', 'osc_3_distortion_amount', 'random_3_tempo', 'lfo_2_delay_time', 'random_1_stereo', 'env_5_attack', 'env_2_attack_power', 'compressor_low_upper_threshold', 'env_2_decay_power', 'osc_3_spectral_morph_spread', 'osc_3_spectral_morph_amount', 'lfo_7_keytrack_tune', 'lfo_3_delay_time', 'lfo_1_fade_time', 'env_3_delay', 'random_4_frequency', 'env_5_delay', 'random_2_sync_type', 'osc_3_on', 'osc_3_unison_detune', 'compressor_band_lower_ratio', 'chorus_on', 'osc_2_pan', 'env_2_sustain', 'lfo_4_keytrack_tune', 'random_4_sync_type', 'eq_on', 'env_5_release_power', 'env_6_release', 'osc_2_spectral_morph_type', 'lfo_5_keytrack_tune', 'osc_2_random_phase', 'osc_3_spectral_unison', 

In [10]:
CORE_COMPONENT_MAP = {
    # Component Mapping (Prefixes)
    "osc": "oscillator",
    "env": "envelope",
    "random": "random_lfo",
    
    # Macro Control Mapping
    "macro_control": "macro",
    
    # Effect Mapping
    "reverb": "reverb",
    "chorus": "chorus",
    "phaser": "phaser",
    "flanger": "flanger",
    "eq": "eq",
    "delay": "delay",
    "compressor": "compressor", # Stays 'compressor' in both, though Set 2 uses specific band terms
    
    # Other Core Modules
    "sample": "sample",
    "wavetables": "wavetables",
    "lfos": "lfos",
    "modulations": "modulations"
}

COMMON_SUFFIX_MAP = {
    # On/Off
    "_on": "_switch",
    
    # Envelope Parameter Mapping
    "_attack": "_attack",
    "_decay": "_decay",
    "_sustain": "_sustain",
    "_release": "_release",
    "_hold": "_hold",
    
    # LFO Keytracking
    "_keytrack_tune": "_tune",
    "_keytrack_transpose": "_transpose",
    "_fade_time": "_fade_in",
    
    # Oscillator Specific
    "_spectral_morph": "_frequency_morph",
    "_random_phase": "_phase_randomization",
    "_frame_spread": "_frame_spread", # Note: Set 2 often uses "unison_frame_spread" for this context
    
    # Effect Mix
    "_dry_wet": "_mix",
    
    # Filter/Effect Keytracking
    "_keytrack": "_key_track",
}

preset_new_settings = {}
for key, value in preset_data["settings"].items():
    new_key = key
    for prefix, mapped_prefix in CORE_COMPONENT_MAP.items():
        if key.startswith(prefix):
            new_key = key.replace(prefix, mapped_prefix, 1)
            break
    for suffix, mapped_suffix in COMMON_SUFFIX_MAP.items():
        if new_key.endswith(suffix):
            new_key = new_key[:-len(suffix)] + mapped_suffix
            break
    preset_new_settings[new_key] = value

# Print common length after remapping
common_keys_remapped = set(preset_new_settings.keys()).intersection(set(vital.parameters.keys()))
print(len(common_keys_remapped))

# Show keys in preset but not in vital parameters after remapping
preset_only_keys_remapped = set(preset_new_settings.keys()) - set(vital.parameters.keys())
print(preset_only_keys_remapped)

# Show keys in vital parameters but not in preset after remapping
vital_only_keys_remapped = set(vital.parameters.keys()) - set(preset_new_settings.keys())
print(vital_only_keys_remapped)

723
{'lfos', 'compressor_band_upper_threshold', 'oscillator_1_spectral_morph_amount', 'delay_aux_frequency', 'compressor_band_lower_threshold', 'filter_1_blend_transpose', 'oscillator_1_unison_blend', 'oscillator_2_frame_spread', 'compressor_low_upper_ratio', 'chorus_spread', 'oscillator_3_spectral_morph_spread', 'oscillator_1_spectral_morph_type', 'lfo_8_delay_time', 'compressor_high_upper_threshold', 'lfo_2_delay_time', 'lfo_5_delay_time', 'sample_phase_randomization', 'compressor_low_lower_threshold', 'sample_key_track', 'compressor_low_upper_threshold', 'oscillator_3_unison_blend', 'reverb_low_shelf_gain', 'oscillator_1_spectral_morph_spread', 'chorus_cutoff', 'lfo_3_delay_time', 'delay_aux_sync', 'lfo_1_delay_time', 'compressor_high_upper_ratio', 'sample', 'compressor_band_lower_ratio', 'lfo_7_delay_time', 'oscillator_1_frame_spread', 'lfo_6_delay_time', 'wavetables', 'oscillator_3_frame_spread', 'oscillator_3_spectral_morph_type', 'oscillator_3_spectral_morph_amount', 'filter_2_b

In [11]:
# All types using getattr(vital,key).type
from collections import Counter
compteur = Counter()
for key in common_keys_remapped:
    compteur[getattr(vital,key).type] += 1
print(compteur)

Counter({<class 'float'>: 326, <class 'bool'>: 240, <class 'str'>: 157})


In [12]:
# All types using getattr(vital,key).type
from collections import Counter
compteur = Counter()
for key in common_keys_remapped:
    if getattr(vital,key).type == str:
        print(f"{key}, {getattr(vital,key)}, {preset_new_settings[key]}")
    if getattr(vital,key).type == bool:
        print(f"{key}, {getattr(vital,key)}, {preset_new_settings[key]}")
print(compteur)

modulation_55_bipolar, False, 0.0
oscillator_2_distortion_type, None, 0.0
modulation_4_bipolar, False, 0.0
modulation_6_bipolar, False, 0.0
envelope_6_release, 0.0899194 secs, 0.5475999712944031
oscillator_2_destination, FILTER 2, 0.0
delay_sync, Tempo, 1.0
envelope_3_hold, 0 secs, 0.0
modulation_38_bipolar, False, 0.0
modulation_11_bipolar, False, 0.0
modulation_40_bypass, False, 0.0
envelope_4_release, 0.0899194 secs, 0.5475999712944031
lfo_1_frequency, 0.5 secs, 1.0
reverb_delay, 0 secs, 0.0
envelope_6_decay, 1 secs, 1.0
oscillator_2_view_2d, On, 1.0
filter_1_style, 12dB, 1.0
portamento_time, 0.000976562 secs, -10.0
lfo_5_fade_in, 0 secs, 0.0
filter_1_cutoff, 0 semitones, 106.69924926757812
random_lfo_4_tempo, 1/4, 8.0
lfo_4_sync, Tempo, 1.0
modulation_41_bipolar, False, 0.0
lfo_5_smooth_mode, True, 1.0
lfo_8_smooth_time, 0.00552427 secs, -7.5
modulation_58_bypass, False, 0.0
modulation_17_stereo, False, 0.0
modulation_52_bipolar, False, 0.0
modulation_28_bipolar, False, 0.0
random_

In [13]:
# Play with the plugin parameters
sound = vital(
  [Message("note_on", note=10), Message("note_off", note=10, time=5)],
  duration=5,
  sample_rate=sample_rate,
)
Audio(sound, rate=sample_rate)

In [14]:
# For all of these keys in common_keys_remapped, set the vital parameter to the preset value
failed = 0
success = 0
skipped = 0

for key in common_keys_remapped:
    try:
        param_type = getattr(vital, key).type
        
        # Skip string parameters
        if param_type == str:
            skipped += 1
            continue
        
        # Convert value based on parameter type
        value = preset_new_settings[key]
        
        if param_type == bool:
            if isinstance(value, str):
                value = value.lower() in ['true', '1', '1.0', 'yes']
            else:
                value = bool(value)
        else:
            # Handle numeric types (float/int)
            value = float(value) if param_type == float else value
        
        # Set the parameter
        setattr(vital, key, value)
        success += 1
        
    except Exception as e:
        print(f"Failed to set {key}: {e}")
        failed += 1

print(f"Skipped: {skipped}, Failed: {failed}, Success: {success}")

Failed to set beats_per_minute: Value received for parameter 'beats_per_minute' (1.5000001192092896) is out of range [20.0None, 300.0None]
Failed to set chorus_delay_2: Value received for parameter 'chorus_delay_2' (-7.0) is out of range [0.976562ms, 19.9999ms]
Failed to set filter_fx_formant_resonance: Value received for parameter 'filter_fx_formant_resonance' (0.8500000238418579) is out of range [30.0%, 100.0%]
Failed to set chorus_delay_1: Value received for parameter 'chorus_delay_1' (-9.0) is out of range [0.976562ms, 19.9999ms]
Failed to set reverb_chorus_frequency: Value received for parameter 'reverb_chorus_frequency' (-2.0) is out of range [0.00390625Hz, 8.0Hz]
Failed to set filter_2_formant_resonance: Value received for parameter 'filter_2_formant_resonance' (0.8500000238418579) is out of range [30.0%, 100.0%]
Failed to set filter_1_formant_resonance: Value received for parameter 'filter_1_formant_resonance' (0.8500000238418579) is out of range [30.0%, 100.0%]
Failed to set v

In [15]:
# Play with the plugin parameters
sound = vital(
  [Message("note_on", note=10), Message("note_off", note=10, time=5)],
  duration=5,
  sample_rate=sample_rate,
)
Audio(sound, rate=sample_rate)

In [ ]:
from pedalboard import load_plugin
import json
import pickle

# Load the plugin
vital = load_plugin("/home/benjamin/Documents/work/Synthetizers-parameters-estimation/plugins/Surge XTz.vst3")

# This will pause the script until you close the VST window
print("Opening plugin editor... Close the editor window to continue.")
vital.show_editor() 

print("Reading parameters after manual edits...")

pickle.dump(vital.parameters)

print(f"Read parameters: {read_success} succeeded, {read_failure} failed/skipped.")

# Serialize successfully read parameters to JSON
if param_value_dict:
    with open("params.json", "w") as f:
        json.dump(param_value_dict, f, indent=2)
    print(f"Parameters serialized successfully to params.json ({len(param_value_dict)} parameters).")
else:
    print("No serializable parameters were read.")

# --- Test Reloading the Parameters ---
print("Reloading parameters from serialized values...")
set_success, set_failure = 0, 0
for parameter_name, serialized_value in param_value_dict.items():
    try:
        setattr(vital, parameter_name, serialized_value)
        set_success += 1
    except Exception as e:
        # This might fail if a parameter is read-only or expects a different type
        print(f"Failed to set {parameter_name}: {e}")
        set_failure += 1

print(f"Reloaded parameters: {set_success} succeeded, {set_failure} failed.")

Opening plugin editor... Close the editor window to continue.
Reading parameters after manual edits...


TypeError: dump() missing required argument 'file' (pos 2)

In [106]:
from pedalboard import load_plugin
import json
import pickle

# Load the plugin
vital = load_plugin("/home/benjamin/Documents/work/Synthetizers-parameters-estimation/plugins/Surge XT.vst3")

# This will pause the script until you close the VST window
print("Opening plugin editor... Close the editor window to continue.")
vital.show_editor() 

print("Reading parameters after manual edits...")

Opening plugin editor... Close the editor window to continue.
Reading parameters after manual edits...


In [ ]:
pickle.dump(vital.parameters, open("vital_params.pkl", "wb"))
print("Parameters saved to vital_params.pkl")

{'m1': <pedalboard.AudioProcessorParameter name="M1: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm2': <pedalboard.AudioProcessorParameter name="M2: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm3': <pedalboard.AudioProcessorParameter name="M3: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm4': <pedalboard.AudioProcessorParameter name="M4: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm5': <pedalboard.AudioProcessorParameter name="M5: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm6': <pedalboard.AudioProcessorParameter name="M6: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm7': <pedalboard.AudioProcessorParameter name="M7: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'm8': <pedalboard.AudioProcessorParameter name="M8: -" discrete raw_value=0 value=0.000000 range=(0.0, 0.0, ?)>, 'send_fx_1_return': <pedalboard.AudioProcessorParameter name="Send FX 1 Return" discrete raw_va

In [ ]:
# Play with the plugin parameters
sample_rate = 44100
sound = vital([Message("note_on", note=72), Message("note_off", note=72, time=2)],
        sample_rate=sample_rate,
        duration=2,
        num_channels=2
)
Audio(sound, rate=sample_rate)

sound2 = vital([Message("note_on", note=50), Message("note_off", note=50, time=2)],
        sample_rate=sample_rate,
        duration=2,
        num_channels=2
)
Audio(sound2, rate=sample_rate)

In [ ]:
# Reload the plugin
vital_reset = load_plugin("/home/benjamin/Documents/work/Synthetizers-parameters-estimation/plugins/Surge XT.vst3")

# Load the parameters
vital_reset.parameters = pickle.load(open("vital_params.pkl", "rb"))

# Play with the reloaded plugin parameters
sample_rate = 44100
sound = vital_reset([Message("note_on", note=72), Message("note_off", note=72, time=2)],
        sample_rate=sample_rate,
        duration=2,
        num_channels=2
)
Audio(sound, rate=sample_rate)

sound2 = vital_reset([Message("note_on", note=50), Message("note_off", note=50, time=2)],
        sample_rate=sample_rate,
        duration=2,
        num_channels=2
)
Audio(sound2, rate=sample_rate)